### Limpieza de la base de datos
Proyecto: Análisis tutelar en temas de salud 1992 - 2019

Autor: Juan Sebastian Muñoz

Objetivo: Limpiar la información de las tutelas.

Fecha de creación: Noviembre de 2019

In [1]:
import nltk                     #Para Análisis del texto
from nltk import word_tokenize
from nltk.corpus import stopwords
import numpy as np
import timeit                   #Para calcular tiempos de ejecución del código
import re                       #Para uso de expresiones regulares
import matplotlib.pyplot as plt #Para realizar los gráficos
import requests                 #Para hacer las solicitudes del codigo fuente de las páginas
from bs4 import BeautifulSoup   #Para transformar el código extraído a formato para poder ser usado en Python
import pandas as pd             #Decarga de pandas para uso de bases de datos
plt.rcParams["figure.figsize"] = [18.0, 8.0]

In [42]:
Tutelas = pd.read_pickle('DB_Tutelas.pkl')
len(Tutelas)

FileNotFoundError: [Errno 2] No such file or directory: 'DB_Tutelas.pkl'

In [ ]:
pat = '>Item </strong>(.*?) <strong>\xa0\xa0\xa0Expediente </strong>\xa0\xa0(.*?)<strong>\xa0\xa0\xa0 Fecha sentencia </strong>\xa0\xa0(.*?)-(.*?)-(.*?) <strong>\xa0\xa0\xa0Sentencia </strong>\xa0\xa0<a href="(.*?)">(.*?)</a> <br/>\n<strong>Magistrado Ponente</strong>:(.*?)<br/>\n<strong>Demandante / Demandado</strong> \xa0\xa0\xa0(.*?)VS(.*?)<br/>\n</p><p align="justify"><strong>Tema:</strong>(.*?\r*\n*.*?\r*\n*.*?\r*\n*.*?\r*\n*.*?)\r*\n*\s*\s*\r*\n*\r*\n*<br/>\n<strong>Recibo Relatoria: </strong> \xa0\xa0(.*?)-(.*?)-(\d+)'
info = []
for i in range (30,38):
    html = requests.get("http://www.corteconstitucional.gov.co/relatoria/radicador/buscar.php?vs=5832&pg="+str(i)+"&ponente=&demandado=&Sentencia=&Tipo=Sentencias&busqueda=salud&conector=AND&segundotema=&anios=Todos").text
    soup = BeautifulSoup(html)
    info.append(re.findall(pat, str(soup)))
    print(len(info))

1
2
3
4


In [3]:
info_lists = [list(elem) for elem in info]
infolists = [list(a) for elem in info_lists for a in elem]
len(infolists)

2036

In [4]:
info_lists = [list(elem) for elem in info]
infolists = [list(a) for elem in info_lists for a in elem]
for i in range(len(infolists)):
    infolists[i][5] = "http://www.corteconstitucional.gov.co/"+infolists[i][5]
infolists

[['3801',
  'T-2276144, T-2279942',
  '2009',
  '09',
  '17',
  'http://www.corteconstitucional.gov.co//relatoria/2009/T-644-09.htm',
  'T-644/09',
  'JUAN CARLOS HENAO PÉREZ            ',
  'MAYERLY CARDENAS Y LIBIA CASADIEGOS ',
  '. FAMISANAR Y COOMEVA EPS',
  '   Salud, vida digna, mínimo vital, se acumulan los expedientes, por guardar unidad de materia. Las actoras interponen acción de tutela solicitando les sea reconocida la licencia de maternidad a que tienen derecho, las EPS accionadas se niegan a realizar dicho pago, por cuanto una de las acccionantes no cotizó en las fechas exigidas por la ley (pago extemporáneo) y por otra parte la segunda accionante no realizó el pago completo de aportes. En cuanto al primer caso la Corte ha establecido que sí se realiza el pago tardío de aportes y la EPS lo recibe, sin haber realizado antes cualquier tipo de requerimiento, se entenderá que la entidad accionada se allanó a la mora del empleador o del cotizante, por lo tanto Coomeva EPS, se 

In [5]:
list_tutelas=[]
for i in range(len(infolists)):
    list_tutelas.append(infolists[i])
    len(list_tutelas)

In [6]:
len(list_tutelas)

2036

In [9]:
Database_tutelas = pd.DataFrame(infolists)
Database_tutelas.columns = ['Item','Expediente','Año','Mes','Día','Link', 'Sentencia', 'Magistrado_Ponente', 'Demandante', 'Demandado', 'Tema', 'Año_R', 'Mes_R', 'Día_R']

In [10]:
#Limpieza de links y formatos especiales dentro de 'tema'
def clean_color(text):
    return re.sub('<span style="color:black;background:#FF8000">.*?</span>', 'salud', text)
Database_tutelas['Tema'] = Database_tutelas['Tema'].apply(clean_color)
def clean_links(text):
    return re.sub('<a.*?a>', '', text)
Database_tutelas['Tema'] = Database_tutelas['Tema'].apply(clean_links)

In [11]:
#Deja solo al magistrado ponente:
def clean_magistrado(text):
    return re.sub('<.*?   ', '', text)
Database_tutelas['Magistrado_Ponente'] = Database_tutelas['Magistrado_Ponente'].apply(clean_magistrado)
Database_tutelas['Magistrado_Ponente'][0]

'JUAN CARLOS HENAO PÉREZ            '

In [12]:
Database_tutelas['Año'] = pd.to_numeric(Database_tutelas['Año'], errors = "coerce")
Database_tutelas['Mes'] = pd.to_numeric(Database_tutelas['Mes'], errors = "coerce")
Database_tutelas['Día'] = pd.to_numeric(Database_tutelas['Día'], errors = "coerce")
Database_tutelas['Año_R'] = pd.to_numeric(Database_tutelas['Año_R'], errors = "coerce")
Database_tutelas['Mes_R'] = pd.to_numeric(Database_tutelas['Mes_R'], errors = "coerce")
Database_tutelas['Día_R'] = pd.to_numeric(Database_tutelas['Día_R'], errors = "coerce")

In [13]:
# Añadir la columna de fecha en formato datetime

Database_tutelas['Fecha'] = pd.to_datetime(Database_tutelas.Año * 10000 + Database_tutelas.Mes * 100 + Database_tutelas.Día, format='%Y%m%d')
Database_tutelas['Fecha_relatoria'] = pd.to_datetime(Database_tutelas.Año_R * 10000 + Database_tutelas.Mes_R * 100 + Database_tutelas.Día_R, format='%Y%m%d')

In [14]:
Database_tutelas

Item                    Expediente   Año  Mes  Día  \
0     3801          T-2276144, T-2279942  2009    9   17   
1     3802                     T-2280417  2009    9   17   
2     3803                     T-2282000  2009    9   17   
3     3804                     T-2284475  2009    9   17   
4     3805                     T-2277821  2009    9   17   
5     3806                     T-2281600  2009    9   17   
6     3807                     T-2281680  2009    9   17   
7     3808                     T-2283221  2009    9   18   
8     3809                     T-2282970  2009    9   21   
9     3810                        OP-124  2009    9   22   
10    3811                        D-7638  2009    9   22   
11    3812                        D-7664  2009    9   22   
12    3813                     T-2248073  2009    9   22   
13    3814                     T-2263995  2009    9   24   
14    3815                     T-2291563  2009    9   24   
15    3816                     T-2309506  2009    9   24   
16    3817                     T-2319136  2009    9   24   
17    3818                     T-2149488  2009    9   28   
18    3819                        D-7628  2009    9   30   
19    3820                     T-2294260  2009   10    1   
20    3821                     T-2226874  2009   10    1   
21    3822                     T-2298579  2009   10    2   
22    3823                     T-2295293  2009   10    2   
23    3824                     T-2291796  2009   10    2   
24    3825                     T-2294645  2009   10    2   
25    3826                     T-2250682  2009   10    2   
26    3827                     T-2288521  2009   10    6   
27    3828                     T-2256577  2009   10    6   
28    3829                     T-2322589  2009   10    6   
29    3830                     T-2300833  2009   10    7   
...    ...                           ...   ...  ...  ...   
2006  5809                     T-7264458  2019    8   13   
2007  5810                       D-12671  2019    8   14   
2008  5811                     T-6718594  2019    8   16   
2009  5812                     T-7248855  2019    8   20   
2010  5813                     T-7045029  2019    8   20   
2011  5814                     T-7118726  2019    8   21   
2012  5815                     T-6820861  2019    8   29   
2013  5816                     T-6700575  2019    8   30   
2014  5817                     T-7102690  2019    8   30   
2015  5818                     T-7327661  2019    9    2   
2016  5819                     T-7318036  2019    9    3   
2017  5820                     T-7292115  2019    9   12   
2018  5821                     T-7349929  2019    9   12   
2019  5822                     T-7367324  2019    9   13   
2020  5823                     T-7128825  2019    9   24   
2021  5824                     T-7078910  2019    9   25   
2022  5825                     T-7162068  2019    9   30   
2023  5826                     T-7350244  2019    9   30   
2024  5827  T-7210348 Y OTROS ACUMULADOS  2019   10    3   
2025  5828                     T-7247104  2019   10    8   
2026  5829                     T-7343448  2019   10    8   
2027  5830                     T-7211119  2019   10    8   
2028  5831                     T-7273545  2019   10   11   
2029  5832                     T-7276111  2019   10   15   
2030  5833                     T-7268969  2019   10   17   
2031  5834                     T-7310345  2019   10   28   
2032  5835   T-7196205 Y OTRO ACUMULADOS  2019   10   28   
2033  5836                     T-7257615  2019   10   29   
2034  5837                     T-7203328  2019   10   29   
2035  5838                     T-7443070  2019   11    6   

                                                   Link Sentencia  \
0     http://www.corteconstitucional.gov.co//relator...  T-644/09   
1     http://www.corteconstitucional.gov.co//relator...  T-646/09   
2     http://www.corteconstitucional.gov.co//relator...  T-647/09   
3     htt

In [15]:
#Quita el doble espacio
def clean_spaces(text):
    return re.sub(' {2,}', '', text)
Database_tutelas['Magistrado_Ponente'] = Database_tutelas['Magistrado_Ponente'].apply(clean_spaces)

In [16]:
#Quita puntos, especialmente para que palabras como E.P.S. no vayan a quedar en tres palabras diferentes
def clean_dot(text):
    return re.sub('\.', '', text)
Database_tutelas['Demandado'] = Database_tutelas['Demandado'].apply(clean_dot)
def clean_comma(text):
    return re.sub(',', ' ', text)
Database_tutelas['Demandado'] = Database_tutelas['Demandado'].apply(clean_comma)

In [17]:
Database_tutelas['Demandado']

0                                 FAMISANAR Y COOMEVA EPS
1                                            COOSALUD ESS
2                                             COOMEVA EPS
3                                           ARP COLPATRIA
4        EMPRESA DE SERVICIOS TEMPORALES GESTIÓN DINAM...
5                                             COOMEVA EPS
6               MINISTERIO DE DEFENSA Y EJERCITO NACIONAL
7                                           EMSSANAR EPSS
8                                 OLEAGINOSAS CARIBÚ LTDA
9            PROYECTO DE LEY 312/08 "LEY SANDRA CEBALLOS"
10                             LEY 755 DE 2002 ARTÍCULO 1
11                          LEY 1151 DE 2007 ARTÍCULO 146
12                           COLMEDICA MEDICINA PREPAGADA
13                                           EMPLEAMOS SA
14              HOSPITAL FEDERICO LLERAS ACOSTA DE IBAGUE
15                        SERVICIOS OCCIDENTALES DE SALUD
16                                            COOMEVA EPS
17            

In [18]:
#Revisar que no hayan duplicados
Database_tutelas.drop_duplicates(subset = ('Sentencia'), inplace = True)
len(Database_tutelas)

2034

Hay 1 duplicado.

In [19]:
# Organizo por fecha

Database_tutelas.sort_values('Fecha', inplace = True)

In [20]:
# Reinicio los índices

Database_tutelas.reset_index(inplace = True, drop = True)
Database_tutelas

Item                    Expediente   Año  Mes  Día  \
0     3801          T-2276144, T-2279942  2009    9   17   
1     3802                     T-2280417  2009    9   17   
2     3803                     T-2282000  2009    9   17   
3     3804                     T-2284475  2009    9   17   
4     3805                     T-2277821  2009    9   17   
5     3806                     T-2281600  2009    9   17   
6     3807                     T-2281680  2009    9   17   
7     3808                     T-2283221  2009    9   18   
8     3809                     T-2282970  2009    9   21   
9     3810                        OP-124  2009    9   22   
10    3811                        D-7638  2009    9   22   
11    3812                        D-7664  2009    9   22   
12    3813                     T-2248073  2009    9   22   
13    3817                     T-2319136  2009    9   24   
14    3816                     T-2309506  2009    9   24   
15    3815                     T-2291563  2009    9   24   
16    3814                     T-2263995  2009    9   24   
17    3818                     T-2149488  2009    9   28   
18    3819                        D-7628  2009    9   30   
19    3820                     T-2294260  2009   10    1   
20    3821                     T-2226874  2009   10    1   
21    3822                     T-2298579  2009   10    2   
22    3823                     T-2295293  2009   10    2   
23    3824                     T-2291796  2009   10    2   
24    3825                     T-2294645  2009   10    2   
25    3826                     T-2250682  2009   10    2   
26    3827                     T-2288521  2009   10    6   
27    3828                     T-2256577  2009   10    6   
28    3829                     T-2322589  2009   10    6   
29    3831                     T-2296233  2009   10    7   
...    ...                           ...   ...  ...  ...   
2004  5809                     T-7264458  2019    8   13   
2005  5810                       D-12671  2019    8   14   
2006  5811                     T-6718594  2019    8   16   
2007  5812                     T-7248855  2019    8   20   
2008  5813                     T-7045029  2019    8   20   
2009  5814                     T-7118726  2019    8   21   
2010  5815                     T-6820861  2019    8   29   
2011  5816                     T-6700575  2019    8   30   
2012  5817                     T-7102690  2019    8   30   
2013  5818                     T-7327661  2019    9    2   
2014  5819                     T-7318036  2019    9    3   
2015  5820                     T-7292115  2019    9   12   
2016  5821                     T-7349929  2019    9   12   
2017  5822                     T-7367324  2019    9   13   
2018  5823                     T-7128825  2019    9   24   
2019  5824                     T-7078910  2019    9   25   
2020  5825                     T-7162068  2019    9   30   
2021  5826                     T-7350244  2019    9   30   
2022  5827  T-7210348 Y OTROS ACUMULADOS  2019   10    3   
2023  5828                     T-7247104  2019   10    8   
2024  5829                     T-7343448  2019   10    8   
2025  5830                     T-7211119  2019   10    8   
2026  5831                     T-7273545  2019   10   11   
2027  5832                     T-7276111  2019   10   15   
2028  5833                     T-7268969  2019   10   17   
2029  5834                     T-7310345  2019   10   28   
2030  5835   T-7196205 Y OTRO ACUMULADOS  2019   10   28   
2031  5837                     T-7203328  2019   10   29   
2032  5836                     T-7257615  2019   10   29   
2033  5838                     T-7443070  2019   11    6   

                                                   Link Sentencia  \
0     http://www.corteconstitucional.gov.co//relator...  T-644/09   
1     http://www.corteconstitucional.gov.co//relator...  T-646/09   
2     http://www.corteconstitucional.gov.co//relator...  T-647/09   
3     htt

In [21]:
#Defino puntuación para eliminarla
puntuacion = '!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~–¡¿”“•\r´–¡¿”“•\r´º'
puntuacion

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~–¡¿”“•\r´–¡¿”“•\r´º'

In [22]:
#Defino una función que elimine la puntuación
def no_punt(string):
    transtable = string.maketrans('', '', puntuacion)
    return string.translate(transtable)
Database_tutelas['Tutela_no_punt'] = Database_tutelas['Tema'].apply(no_punt)


In [23]:
#Paso a minúsculas todas las letras
Database_tutelas['Tutela_no_punt'] = Database_tutelas['Tutela_no_punt'].apply(str.lower)

In [24]:
Database_tutelas['Demandado_no_punt'] = Database_tutelas['Demandado'].apply(no_punt)
Database_tutelas['Demandado_no_punt'] = Database_tutelas['Demandado_no_punt'].apply(str.lower)

In [25]:
for i in range(len(Database_tutelas)):
    print(Database_tutelas['Tema'][i])

<br/>
   Salud, vida digna. La accionante obra como representante de su menor hija la cual tiene una mala oclusión dental, esto le ha ocasionado problemas de adaptación en su entorno social ya que la niña es rechazada en su colegio por este defecto, la madre de la menor acudió a un centro odontológico no adscrito a la EPS, en el cual se le sugirió el tratamiento de ortodoncia preventiva, la EPS se niega a realizar dicho tratamiento y sugirió que sea valorada por un ESTOMATOLOGO ORAL para poder establecer con mayor precisión la patología de la menor. La Sala encuentra cumplida le exigencia de que la falta del procedimiento, excluido por la reglamentación legal, amenaza los derechos fundamentales de la menor, por lo tanto ordena a la EPS  que autorice la remisión de la niña al especialista en salud oral, para que sea valorada y se le inicie el tratamiento requerido. Concedida.
   Salud, seguridad social, petición. La accionante fue sometida a la extirpación de la vesícula, después de est

 DERECHO FUNDAMENTAL A MORIR DIGNAMENTE. CASO EN QUE SE SOLICITO APLICAR EUTANASIA A JOVEN CON ENFERMEDAD TERMINAL. La accionante, actuando como agente oficiosa de una hija de 24 años de edad que fue diagnosticada con un  cáncer agresivo en etapa terminal, atribuye la vulneración de derechos fundamentales a la falta de práctica del procedimiento de eutanasia que fue solicitado,  por cuanto  los diferentes tratamientos recibidos no fueron efectivos para curar la enfermedad y el pronóstico de vida era limitado.  La entidad negó el procedimiento argumentando que no contaba con un médico especialista en oncología que permitiera conformar un Comité Científico Interdisciplinario.  Se analizan los siguientes temas:  1º. El hecho superado y el daño consumado.  2º. La evolución del derecho fundamental a morir dignamente en Colombia y, 3º. La imposición de barreras administrativas y la vulneración de los derechos fundamentales a la salud y a la vida en condiciones dignas.  A pesar de que el proc

In [26]:
Database_tutelas

Item                    Expediente   Año  Mes  Día  \
0     3801          T-2276144, T-2279942  2009    9   17   
1     3802                     T-2280417  2009    9   17   
2     3803                     T-2282000  2009    9   17   
3     3804                     T-2284475  2009    9   17   
4     3805                     T-2277821  2009    9   17   
5     3806                     T-2281600  2009    9   17   
6     3807                     T-2281680  2009    9   17   
7     3808                     T-2283221  2009    9   18   
8     3809                     T-2282970  2009    9   21   
9     3810                        OP-124  2009    9   22   
10    3811                        D-7638  2009    9   22   
11    3812                        D-7664  2009    9   22   
12    3813                     T-2248073  2009    9   22   
13    3817                     T-2319136  2009    9   24   
14    3816                     T-2309506  2009    9   24   
15    3815                     T-2291563  2009    9   24   
16    3814                     T-2263995  2009    9   24   
17    3818                     T-2149488  2009    9   28   
18    3819                        D-7628  2009    9   30   
19    3820                     T-2294260  2009   10    1   
20    3821                     T-2226874  2009   10    1   
21    3822                     T-2298579  2009   10    2   
22    3823                     T-2295293  2009   10    2   
23    3824                     T-2291796  2009   10    2   
24    3825                     T-2294645  2009   10    2   
25    3826                     T-2250682  2009   10    2   
26    3827                     T-2288521  2009   10    6   
27    3828                     T-2256577  2009   10    6   
28    3829                     T-2322589  2009   10    6   
29    3831                     T-2296233  2009   10    7   
...    ...                           ...   ...  ...  ...   
2004  5809                     T-7264458  2019    8   13   
2005  5810                       D-12671  2019    8   14   
2006  5811                     T-6718594  2019    8   16   
2007  5812                     T-7248855  2019    8   20   
2008  5813                     T-7045029  2019    8   20   
2009  5814                     T-7118726  2019    8   21   
2010  5815                     T-6820861  2019    8   29   
2011  5816                     T-6700575  2019    8   30   
2012  5817                     T-7102690  2019    8   30   
2013  5818                     T-7327661  2019    9    2   
2014  5819                     T-7318036  2019    9    3   
2015  5820                     T-7292115  2019    9   12   
2016  5821                     T-7349929  2019    9   12   
2017  5822                     T-7367324  2019    9   13   
2018  5823                     T-7128825  2019    9   24   
2019  5824                     T-7078910  2019    9   25   
2020  5825                     T-7162068  2019    9   30   
2021  5826                     T-7350244  2019    9   30   
2022  5827  T-7210348 Y OTROS ACUMULADOS  2019   10    3   
2023  5828                     T-7247104  2019   10    8   
2024  5829                     T-7343448  2019   10    8   
2025  5830                     T-7211119  2019   10    8   
2026  5831                     T-7273545  2019   10   11   
2027  5832                     T-7276111  2019   10   15   
2028  5833                     T-7268969  2019   10   17   
2029  5834                     T-7310345  2019   10   28   
2030  5835   T-7196205 Y OTRO ACUMULADOS  2019   10   28   
2031  5837                     T-7203328  2019   10   29   
2032  5836                     T-7257615  2019   10   29   
2033  5838                     T-7443070  2019   11    6   

                                                   Link Sentencia  \
0     http://www.corteconstitucional.gov.co//relator...  T-644/09   
1     http://www.corteconstitucional.gov.co//relator...  T-646/09   
2     http://www.corteconstitucional.gov.co//relator...  T-647/09   
3     htt

In [27]:
#Creo una lista de tokens
Database_tutelas['Tutela_tkn'] = Database_tutelas['Tutela_no_punt'].apply(word_tokenize)
Database_tutelas['Demandado_tkn'] = Database_tutelas['Demandado_no_punt'].apply(word_tokenize)

In [28]:
# Adquiero las stopwords en español y las elimino
stopwords_esp = stopwords.words('spanish')
def no_stopwords(tokens):
    return [p for p in tokens if p not in stopwords_esp]

In [29]:
Database_tutelas

Item                    Expediente   Año  Mes  Día  \
0     3801          T-2276144, T-2279942  2009    9   17   
1     3802                     T-2280417  2009    9   17   
2     3803                     T-2282000  2009    9   17   
3     3804                     T-2284475  2009    9   17   
4     3805                     T-2277821  2009    9   17   
5     3806                     T-2281600  2009    9   17   
6     3807                     T-2281680  2009    9   17   
7     3808                     T-2283221  2009    9   18   
8     3809                     T-2282970  2009    9   21   
9     3810                        OP-124  2009    9   22   
10    3811                        D-7638  2009    9   22   
11    3812                        D-7664  2009    9   22   
12    3813                     T-2248073  2009    9   22   
13    3817                     T-2319136  2009    9   24   
14    3816                     T-2309506  2009    9   24   
15    3815                     T-2291563  2009    9   24   
16    3814                     T-2263995  2009    9   24   
17    3818                     T-2149488  2009    9   28   
18    3819                        D-7628  2009    9   30   
19    3820                     T-2294260  2009   10    1   
20    3821                     T-2226874  2009   10    1   
21    3822                     T-2298579  2009   10    2   
22    3823                     T-2295293  2009   10    2   
23    3824                     T-2291796  2009   10    2   
24    3825                     T-2294645  2009   10    2   
25    3826                     T-2250682  2009   10    2   
26    3827                     T-2288521  2009   10    6   
27    3828                     T-2256577  2009   10    6   
28    3829                     T-2322589  2009   10    6   
29    3831                     T-2296233  2009   10    7   
...    ...                           ...   ...  ...  ...   
2004  5809                     T-7264458  2019    8   13   
2005  5810                       D-12671  2019    8   14   
2006  5811                     T-6718594  2019    8   16   
2007  5812                     T-7248855  2019    8   20   
2008  5813                     T-7045029  2019    8   20   
2009  5814                     T-7118726  2019    8   21   
2010  5815                     T-6820861  2019    8   29   
2011  5816                     T-6700575  2019    8   30   
2012  5817                     T-7102690  2019    8   30   
2013  5818                     T-7327661  2019    9    2   
2014  5819                     T-7318036  2019    9    3   
2015  5820                     T-7292115  2019    9   12   
2016  5821                     T-7349929  2019    9   12   
2017  5822                     T-7367324  2019    9   13   
2018  5823                     T-7128825  2019    9   24   
2019  5824                     T-7078910  2019    9   25   
2020  5825                     T-7162068  2019    9   30   
2021  5826                     T-7350244  2019    9   30   
2022  5827  T-7210348 Y OTROS ACUMULADOS  2019   10    3   
2023  5828                     T-7247104  2019   10    8   
2024  5829                     T-7343448  2019   10    8   
2025  5830                     T-7211119  2019   10    8   
2026  5831                     T-7273545  2019   10   11   
2027  5832                     T-7276111  2019   10   15   
2028  5833                     T-7268969  2019   10   17   
2029  5834                     T-7310345  2019   10   28   
2030  5835   T-7196205 Y OTRO ACUMULADOS  2019   10   28   
2031  5837                     T-7203328  2019   10   29   
2032  5836                     T-7257615  2019   10   29   
2033  5838                     T-7443070  2019   11    6   

                                                   Link Sentencia  \
0     http://www.corteconstitucional.gov.co//relator...  T-644/09   
1     http://www.corteconstitucional.gov.co//relator...  T-646/09   
2     http://www.corteconstitucional.gov.co//relator...  T-647/09   
3     htt

In [30]:
#Agrego una columna para la tutela y el demandado sin stopwords
Database_tutelas['Tutela_nsw'] = Database_tutelas['Tutela_tkn'].apply(no_stopwords)
Database_tutelas['Demandado_nsw'] = Database_tutelas['Demandado_tkn'].apply(no_stopwords)

In [31]:
Database_tutelas

Item                    Expediente   Año  Mes  Día  \
0     3801          T-2276144, T-2279942  2009    9   17   
1     3802                     T-2280417  2009    9   17   
2     3803                     T-2282000  2009    9   17   
3     3804                     T-2284475  2009    9   17   
4     3805                     T-2277821  2009    9   17   
5     3806                     T-2281600  2009    9   17   
6     3807                     T-2281680  2009    9   17   
7     3808                     T-2283221  2009    9   18   
8     3809                     T-2282970  2009    9   21   
9     3810                        OP-124  2009    9   22   
10    3811                        D-7638  2009    9   22   
11    3812                        D-7664  2009    9   22   
12    3813                     T-2248073  2009    9   22   
13    3817                     T-2319136  2009    9   24   
14    3816                     T-2309506  2009    9   24   
15    3815                     T-2291563  2009    9   24   
16    3814                     T-2263995  2009    9   24   
17    3818                     T-2149488  2009    9   28   
18    3819                        D-7628  2009    9   30   
19    3820                     T-2294260  2009   10    1   
20    3821                     T-2226874  2009   10    1   
21    3822                     T-2298579  2009   10    2   
22    3823                     T-2295293  2009   10    2   
23    3824                     T-2291796  2009   10    2   
24    3825                     T-2294645  2009   10    2   
25    3826                     T-2250682  2009   10    2   
26    3827                     T-2288521  2009   10    6   
27    3828                     T-2256577  2009   10    6   
28    3829                     T-2322589  2009   10    6   
29    3831                     T-2296233  2009   10    7   
...    ...                           ...   ...  ...  ...   
2004  5809                     T-7264458  2019    8   13   
2005  5810                       D-12671  2019    8   14   
2006  5811                     T-6718594  2019    8   16   
2007  5812                     T-7248855  2019    8   20   
2008  5813                     T-7045029  2019    8   20   
2009  5814                     T-7118726  2019    8   21   
2010  5815                     T-6820861  2019    8   29   
2011  5816                     T-6700575  2019    8   30   
2012  5817                     T-7102690  2019    8   30   
2013  5818                     T-7327661  2019    9    2   
2014  5819                     T-7318036  2019    9    3   
2015  5820                     T-7292115  2019    9   12   
2016  5821                     T-7349929  2019    9   12   
2017  5822                     T-7367324  2019    9   13   
2018  5823                     T-7128825  2019    9   24   
2019  5824                     T-7078910  2019    9   25   
2020  5825                     T-7162068  2019    9   30   
2021  5826                     T-7350244  2019    9   30   
2022  5827  T-7210348 Y OTROS ACUMULADOS  2019   10    3   
2023  5828                     T-7247104  2019   10    8   
2024  5829                     T-7343448  2019   10    8   
2025  5830                     T-7211119  2019   10    8   
2026  5831                     T-7273545  2019   10   11   
2027  5832                     T-7276111  2019   10   15   
2028  5833                     T-7268969  2019   10   17   
2029  5834                     T-7310345  2019   10   28   
2030  5835   T-7196205 Y OTRO ACUMULADOS  2019   10   28   
2031  5837                     T-7203328  2019   10   29   
2032  5836                     T-7257615  2019   10   29   
2033  5838                     T-7443070  2019   11    6   

                                                   Link Sentencia  \
0     http://www.corteconstitucional.gov.co//relator...  T-644/09   
1     http://www.corteconstitucional.gov.co//relator...  T-646/09   
2     http://www.corteconstitucional.gov.co//relator...  T-647/09   
3     htt

In [32]:
#Paso a texto los tokens de los demandados y de las tutelas
Database_tutelas['Tutela_text'] = Database_tutelas['Tutela_nsw'].apply(nltk.Text)
Database_tutelas['Demandado_text'] = Database_tutelas['Demandado_nsw'].apply(nltk.Text)

In [33]:
Database_tutelas.loc[235:241]

Item Expediente   Año  Mes  Día  \
235  4039  T-2542631  2010    6   16   
236  4040  T-2548704  2010    6   16   
237  4037  T-2535667  2010    6   16   
238  4036  T-2552729  2010    6   16   
239  4035  T-2542501  2010    6   16   
240  4034  T-2534495  2010    6   16   
241  4033  T-2554398  2010    6   16   

                                                  Link Sentencia  \
235  http://www.corteconstitucional.gov.co//relator...  T-477/10   
236  http://www.corteconstitucional.gov.co//relator...  T-480/10   
237  http://www.corteconstitucional.gov.co//relator...  T-475/10   
238  http://www.corteconstitucional.gov.co//relator...  T-472/10   
239  http://www.corteconstitucional.gov.co//relator...  T-471/10   
240  http://www.corteconstitucional.gov.co//relator...  T-470/10   
241  http://www.corteconstitucional.gov.co//relator...  T-469/10   

             Magistrado_Ponente                     Demandante  \
235     JUAN CARLOS HENAO PÉREZ    ISMAEL ALBERTO PARADA PAEZ    
236     JUAN CARLOS HENAO PÉREZ      MARLENY ALVAREZ RESTREPO    
237     JUAN CARLOS HENAO PÉREZ  MARTIN LEYTON AGUILAR Y OTRA    
238  JORGE IVÁN PALACIO PALACIO           LIBARDO DIAZ MORENO    
239  JORGE IVÁN PALACIO PALACIO             SOFIA RUBIO DURAN    
240  JORGE IVÁN PALACIO PALACIO      ALEXANDER ZORRILLO TIQUE    
241  JORGE IVÁN PALACIO PALACIO   HERNAN ANTONIO RUIZ CASTAÑO    

                                           Demandado  ...      Fecha  \
235                                     SOLSALUD EPS  ... 2010-06-16   
236                                     COOSALUD EPS  ... 2010-06-16   
237                            COMFENALCO ARS Y OTRO  ... 2010-06-16   
238   ALCALDIA DE VILLAVICENCIO Y VILLAVIVIENDA EICE  ... 2010-06-16   
239                                        NUEVA EPS  ... 2010-06-16   
240           MINISTERIO DE DEFENSA NACIONAL Y OTROS  ... 2010-06-16   
241                   MINISTERIO DE DEFENSA NACIONAL  ... 2010-06-16   

     Fecha_relatoria                                     Tutela_no_punt  \
235       2010-10-14     salud vida digna el actor sufre de cáncer d...   
236       2011-01-31     igualdad debido proceso trabajo protección ...   
237       2010-09-08     salud vida digna los accionantes actúan en ...   
238       2010-08-25     salud vida digna la accionante sufre de art...   
239       2010-08-30     salud vida digna la accionante sufre de art...   
240       2010-10-20     trabajo mínimo vital igualdad el accionante...   
241       2010-08-25     petición salud seguridad social mínimo vita...   

                                   Demandado_no_punt  \
235                                     solsalud eps   
236                                     coosalud eps   
237                            comfenalco ars y otro   
238   alcaldia de villavicencio y villavivienda eice   
239                                        nueva eps   
240           ministerio de defensa nacional y otros   
241                   ministerio de defensa nacional   

                                            Tutela_tkn  \
235  [salud, vida, digna, el, actor, sufre, de, cán...   
236  [igualdad, debido, proceso, trabajo, protecció...   
237  [salud, vida, digna, los, accionantes, actúan,...   
238  [salud, vida, digna, la, accionante, sufre, de...   
239  [salud, vida, digna, la, accionante, sufre, de...   
240  [trabajo, mínimo, vital, igualdad, el, acciona...   
241  [petición, salud, seguridad, social, mínimo, v...   

                                         Demandado_tkn  \
235                                    [solsalud, eps]   
236                                    [coosalud, eps]   
237                         [comfenalco, ars, y, otro]   
238  [alcaldia, de, villavicencio, y, villavivienda...   
239                                       [nueva, eps]   
240      [ministerio, de, defensa, nacional, y, otros]   
241                [ministerio, de, defensa, nacional]   

                                            Tutela_ns

In [34]:
Database_tutelas['Respuesta'] =[x for x in range (len(Database_tutelas))]

In [35]:
# Se intenta identificar si la tutela fue Concedida, concedida parcialmente, negada, etc.
# Negada = -1
# Concedida Parcialmente = 0.5
# Concedida, AMPARADA = 1
# Hecho superado = 0
# Improcedencia = 2
# Denegar = 3
# Tutelan los derechos = 4
# EXEQUIBILIDAD CONDICIONADA = 5
# Exequibilidad = 6
# Inhibe = 7
# DAÑO CONSUMADO = 8
# CARENCIA ACTUAL DE OBJETO = 9
# CONFIRMA PARCIALMENTE =10
# Se reitera = 11
# Inexequible = 12
# Someterse a lo resuleto = 13
# No procede = 14

for i in range(len(Database_tutelas)):
    if str(Database_tutelas['Tema'][i]).find(' NEGADA.<br/>') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = '-1'
    elif str(Database_tutelas['Tema'][i]).find(' NEGADA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find('<br/>NEGADA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find('<br/>NEGADA.') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find('\r<br/>NEGADA\r<br/>') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find(' NEGARON ') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find(' NEGÓ ') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find(' NEGAR ') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find('NIEGA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find(' NIEG') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find(' NEGAD.') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = -1
    elif str(Database_tutelas['Tema'][i]).find('HECHO SUPERADO') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 0
    elif str(Database_tutelas['Tema'][i]).find('CONCEDIDA PARCIALMENTE.<br/>') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 0.5
    elif str(Database_tutelas['Tema'][i]).find('CONCEDIDA.<br/>') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find(' CONCED') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('e conced') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('AMPAR') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('TUTELÓ') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('Se TUTELA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('TUTELAR') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('OTORGA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    elif str(Database_tutelas['Tema'][i]).find('IMPROCEDENCIA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 2
    elif str(Database_tutelas['Tema'][i]).find('IMPROCEDENTE') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 2
    elif str(Database_tutelas['Tema'][i]).find('DENIEG.') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 3
    elif str(Database_tutelas['Tema'][i]).find('DENIEGA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 3
    elif str(Database_tutelas['Tema'][i]).find(' DENEG') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 3
    elif str(Database_tutelas['Tema'][i]).find(' TUTELAN') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 4
    elif str(Database_tutelas['Tema'][i]).find(' EXEQUIBILIDAD CONDICIONADA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 5
    elif str(Database_tutelas['Tema'][i]).find(' EXEQUIBLE') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 6
    elif str(Database_tutelas['Tema'][i]).find(' EXEQUIBLE.') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 6
    elif str(Database_tutelas['Tema'][i]).find(' EXEQUIBILIDAD') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 6
    elif str(Database_tutelas['Tema'][i]).find('INHIBE') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 7
    elif str(Database_tutelas['Tema'][i]).find('INHIBIDA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 7
    elif str(Database_tutelas['Tema'][i]).find('INHIBID.') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 7
    elif str(Database_tutelas['Tema'][i]).find('DAÑO CONSUMADO') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 8
    elif str(Database_tutelas['Tema'][i]).find('CARENCIA ACTUAL DE OBJETO') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 9
    elif str(Database_tutelas['Tema'][i]).find('carencia actual de objeto') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 9
    elif str(Database_tutelas['Tema'][i]).find('CONFIRMA PARCIALMENTE') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 10
    elif str(Database_tutelas['Tema'][i]).find('Se reitera') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 11
    elif str(Database_tutelas['Tema'][i]).find('INEXEQUIBLE') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 12
    elif str(Database_tutelas['Tema'][i]).find('ESTARSE A LO RESUELTO') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 13
    elif str(Database_tutelas['Tema'][i]).find('Se declara la improcedencia') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 14
    elif str(Database_tutelas['Tema'][i]).find('es improcedente') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 14
    elif str(Database_tutelas['Tema'][i]).find('TUTELA') >= 1:
        Database_tutelas.loc[[i], 'Respuesta'] = 1
    
    else:
        Database_tutelas.loc[[i], 'Respuesta'] = 'NA'

In [36]:
Database_tutelas.loc[54]

Item                                                               3855
Expediente                                                    T-2316604
Año                                                                2009
Mes                                                                  10
Día                                                                  29
Link                  http://www.corteconstitucional.gov.co//relator...
Sentencia                                                      T-773/09
Magistrado_Ponente                        HUMBERTO ANTONIO SIERRA PORTO
Demandante                                 JUANA MARIA DUEÑAS VILLAMIL 
Demandado                           INSTITUO DE SEGUROS SOCIALES Y OTRO
Tema                     Debido proceso, mínimo vital, seguridad soc...
Año_R                                                              2009
Mes_R                                                                11
Día_R                                                           

In [37]:
for i in range (len(Database_tutelas)):
    if Database_tutelas['Respuesta'][i] == 'NA':
        print(Database_tutelas['Item'][i] + '-' + Database_tutelas['Respuesta'][i])

3802-NA
3803-NA
3804-NA
3805-NA
3806-NA
3807-NA
3808-NA
3809-NA
3810-NA
3811-NA
3813-NA
3817-NA
3816-NA
3815-NA
3814-NA
3818-NA
3819-NA
3820-NA
3822-NA
3824-NA
3825-NA
3826-NA
3827-NA
3829-NA
3831-NA
3832-NA
3833-NA
3834-NA
3835-NA
3836-NA
3837-NA
3838-NA
3839-NA
3840-NA
3841-NA
3842-NA
3843-NA
3844-NA
3845-NA
3847-NA
3848-NA
3849-NA
3850-NA
3851-NA
3852-NA
3853-NA
3855-NA
3857-NA
3858-NA
3859-NA
3861-NA
3860-NA
3863-NA
3862-NA
3864-NA
3865-NA
3866-NA
3867-NA
3868-NA
3869-NA
3870-NA
3871-NA
3872-NA
3876-NA
3877-NA
3874-NA
3879-NA
3880-NA
3883-NA
3884-NA
3885-NA
3886-NA
3887-NA
3888-NA
3889-NA
3894-NA
3893-NA
3891-NA
3892-NA
3895-NA
3896-NA
3898-NA
3900-NA
3901-NA
3902-NA
3903-NA
3904-NA
3905-NA
3908-NA
3907-NA
3910-NA
3911-NA
3912-NA
3914-NA
3915-NA
3916-NA
3917-NA
3918-NA
3919-NA
3920-NA
3921-NA
3926-NA
3925-NA
3927-NA
3923-NA
3922-NA
3924-NA
3928-NA
3929-NA
3930-NA
3931-NA
3932-NA
3934-NA
3935-NA
3936-NA
3937-NA
3938-NA
3939-NA
3940-NA
3941-NA
3942-NA
3944-NA
3945-NA
3947-NA
3948-NA


In [38]:
Database_tutelas.to_pickle('DbTutelas.pkl')